<a href="https://colab.research.google.com/github/ThiagoSViana/Infnet-Project/blob/main/Coleta_de_dados_Toronto.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

#Thiago Viana Project: Where to live in Toronto? 
##Choosing a place in Toronto based on data



###The problem!

You are planning immigration to Toronto, Canada, for better life prospects like education, earnings, security and many more. You live in Brazil and love your neighbourhood mainly because of all the great amenities and venues that exist in your neighborhood such as food centres, pharmacies, schools, markets, shopping malls, parks, hospitals and so on. You want to know which neighborhood will be economical and similar to your current neighborhood in Brazil.

Objective

This project is targeted to people interested in immigrating to Toronto, CA,  especially from Brazil as lots of Brazilians have been immigrating in past years and it aims to provide a bird view of variation of housing prices as neighborhood and also the available venues and amenities.

In [ ]:
!pip install opendatasets

In [ ]:
import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import numpy as np
import random
import json 
import requests
import geopy.geocoders as geocoder
import folium
import matplotlib.pyplot as plt
import matplotlib.cm as cm
import matplotlib.colors as colors
import seaborn as sns
import os 
import tqdm 
import warnings 
warnings.filterwarnings('ignore')

from bs4 import BeautifulSoup
from pandas.io.json import json_normalize
from sklearn.cluster import KMeans
from geopy.geocoders import Nominatim
from tqdm._tqdm_notebook import tqdm_notebook
from geopy.extra.rate_limiter import RateLimiter
from yellowbrick.cluster import KElbowVisualizer
from folium import plugins
from folium.plugins import MiniMap

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
url = "https://en.wikipedia.org/w/index.php?title=List_of_postal_codes_of_Canada:_M&oldid=942655364"
res = requests.get(url)
soup = BeautifulSoup(res.content,'lxml')
table = soup.find_all('table')[0]
df = pd.read_html(str(table))
data = pd.read_json(df[0].to_json(orient='records'))

data.head()

Postcode           Borough     Neighbourhood
0      M1A      Not assigned      Not assigned
1      M2A      Not assigned      Not assigned
2      M3A        North York         Parkwoods
3      M4A        North York  Victoria Village
4      M5A  Downtown Toronto      Harbourfront

In [ ]:
#Removing all the 'Not assigned' rows
data.replace("Not assigned", np.nan, inplace = True) # First: changing Not assigned to NaN
data.dropna(inplace=True) # and then drop all NaN rows
data.set_index("Postcode", inplace=True) # setting index to Postal Code
data.reset_index(inplace=True) # reset index, so that index count restarts
data.head(11)

Postcode           Borough     Neighbourhood
0       M3A        North York         Parkwoods
1       M4A        North York  Victoria Village
2       M5A  Downtown Toronto      Harbourfront
3       M6A        North York  Lawrence Heights
4       M6A        North York    Lawrence Manor
5       M7A  Downtown Toronto      Queen's Park
6       M9A         Etobicoke         Islington
7       M1B       Scarborough             Rouge
8       M1B       Scarborough           Malvern
9       M3B        North York   Don Mills North
10      M4B         East York  Woodbine Gardens

In [ ]:
data.shape

(210, 3)

In [ ]:
coords_Cor = pd.read_csv('/content/drive/MyDrive/Geospatial_Coordinates_Cor.csv')
coords_Cor.head()

Postcode   Latitude  Longitude
0      M1B  43.806686 -79.194353
1      M1C  43.784535 -79.160497
2      M1E  43.763573 -79.188711
3      M1G  43.770992 -79.216917
4      M1H  43.773136 -79.239476

In [ ]:
toronto_data_merge= pd.merge(data, coords_Cor, on='Postcode')
toronto_data_merge.head()

Postcode           Borough     Neighbourhood   Latitude  Longitude
0      M3A        North York         Parkwoods  43.753259 -79.329656
1      M4A        North York  Victoria Village  43.725882 -79.315572
2      M5A  Downtown Toronto      Harbourfront  43.654260 -79.360636
3      M6A        North York  Lawrence Heights  43.718518 -79.464763
4      M6A        North York    Lawrence Manor  43.718518 -79.464763

In [ ]:
#toronto_data_merge = toronto_data_merge.to_csv('/content/drive/MyDrive/toronto_data_merge.csv', index=False)
toronto_data_merge_ll = pd.read_csv('/content/drive/MyDrive/toronto_data_merge.csv')
toronto_data_merge_ll.head()

Postcode           Borough     Neighbourhood   Latitude  Longitude
0      M3A        North York         Parkwoods  43.753259 -79.329656
1      M4A        North York  Victoria Village  43.725882 -79.315572
2      M5A  Downtown Toronto      Harbourfront  43.654260 -79.360636
3      M6A        North York  Lawrence Heights  43.718518 -79.464763
4      M6A        North York    Lawrence Manor  43.718518 -79.464763

In [ ]:
address = 'Toronto, Canada'

geolocator = Nominatim(user_agent="can_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.6534817, -79.3839347.


In [ ]:
CLIENT_ID = 'XVY0YGK3DX5QGHMN2TGSK2EWA55P3JNPIVC5QVW5SGIGUI2L' 
CLIENT_SECRET = 'T53Z3HT4W5DVALRIPBK2DPD4NFOCISMUTMNBLNW13KEJTAIJ'
VERSION = '20191101'

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

In [ ]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            100)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [ ]:
toronto_venues = getNearbyVenues(names=toronto_data_merge['Neighbourhood'],
                                   latitudes=toronto_data_merge['Latitude'],
                                   longitudes=toronto_data_merge['Longitude'],
                                  )

In [ ]:
toronto_venues.groupby('Neighborhood').count()

In [ ]:
# toronto_venues.to_csv('/content/drive/MyDrive/toronto_venues_data_merge.csv', index=False)
toronto_data_merge = pd.read_csv('/content/drive/MyDrive/toronto_venues_data_merge.csv')
toronto_data_merge.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                               
Adelaide                                                             100   
Agincourt                                                              4   
Agincourt North                                                        4   
Albion Gardens                                                        10   
Alderwood                                                              6   
Bathurst Manor                                                        20   
Bathurst Quay                                                         15   
Bayview Village                                                        4   
Beaumond Heights                                                      10   
Bedford Park                                                          24   
Berczy Park                                                           57   
Birch Cliff                                                            4   
Bloordale Gardens                                                     10   
Brockton                                                              25   
Business Reply Mail Processing Centre 969 Eastern                     14   
CFB Toronto                                                            2   
CN Tower                                                              15   
Cabbagetown                                                           43   
Caledonia-Fairbanks                                                    5   
Canada Post Gateway Processing Centre                                 13   
Cedarbrae                                                              7   
Central Bay Street                                                    70   
Chinatown                                                             62   
Christie                                                              14   
Church and Wellesley                                                  83   
Clairlea                                                               9   
Clarks Corners                                                        15   
Cliffcrest                                                             2   
Cliffside                                                              2   
Cliffside West                                                         4   
Cloverdale                                                             1   
Commerce Court                                                       100   
Davisville                                                            36   
Davisville North                                                       9   
Deer Park                                                             13   
Del Ray                                                                4   
Design Exchange                                                      100   
Don Mills North                                                        7   
Don Mills South                                                       19   
Dorset Park                                                            7   
Dovercourt Village                                                    16   
Downsview                                                              4   
Downsview Central                                                      2   
Downsview East                                                         2   
Downsview North                                                       20   
Downsview Northwest                                                    4   
Downsview West                                                         5   
Dufferin                                                              16   
East Birchmount Park                                                   8   
East Toronto                                                           3   
Emery                                                                  2   
Eringate               

In [ ]:
toronto_data_merge.shape

(4186, 7)

In [ ]:
print('There are {} uniques categories.'.format(len(toronto_data_merge['Venue Category'].unique())))

There are 274 uniques categories.


In [ ]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_data_merge[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = toronto_data_merge['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Yoga Studio  Accessories Store  Adult Boutique  Afghan Restaurant  Airport  \
0            0                  0               0                  0        0   
1            0                  0               0                  0        0   
2            0                  0               0                  0        0   
3            0                  0               0                  0        0   
4            0                  0               0                  0        0   

   Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0                   0             0               0                0   
1                   0             0               0                0   
2                   0             0               0                0   
3                   0             0               0                0   
4                   0             0               0                0   

   Airport Terminal  American Restaurant  Antique Shop  Aquarium  Art Gallery  \
0                 0                    0             0         0            0   
1                 0                    0             0         0            0   
2                 0                    0             0         0            0   
3                 0                    0             0         0            0   
4                 0                    0             0         0            0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auto Garage  \
0                    0                 0                   0            0   
1                    0                 0                   0            0   
2                    0                 0                   0            0   
3                    0                 0                   0            0   
4                    0                 0                   0            0   

   Auto Workshop  BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  \
0              0          0           0           0       0     0    0   
1              0          0           0           0       0     0    0   
2              0          0           0           0       0     0    0   
3              0          0           0           0       0     0    0   
4              0          0           0           0       0     0    0   

   Baseball Field  Baseball Stadium  Basketball Court  Basketball Stadium  \
0               0                 0                 0                   0   
1               0                 0                 0                   0   
2               0                 0                 0                   0   
3               0                 0                 0                   0   
4               0                 0                 0                   0   

   Beach  Bed & Breakfast  Beer Bar  Beer Store  Belgian Restaurant  \
0      0                0         0           0                   0   
1      0                0         0           0                   0   
2      0                0         0           0                   0   
3      0                0         0           0                   0   
4      0                0         0           0                   0   

   Bike Shop  Bistro  Boat or Ferry  Bookstore  Boutique  \
0          0       0              0          0         0   
1          0       0              0          0         0   
2          0       0              0          0         0   
3          0       0              0          0         0   
4          0       0              0          0         0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0                     0               0        0            0   
1                     0               0        0            0   
2                     0               0        0            0   
3                     0               0        0            0   
4                     0               0        0            0   

   Bubble Tea Shop  Building  Burger Joint  Bu

In [ ]:
toronto_onehot.shape

(4186, 274)

In [ ]:
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
#toronto_grouped.to_csv('/content/drive/MyDrive/toronto_grouped.csv')
#toronto_grouped = pd.read_csv('/content/drive/MyDrive/toronto_grouped.csv')
toronto_grouped

Neighborhood  Yoga Studio  \
0                                             Adelaide     0.000000   
1                                            Agincourt     0.000000   
2                                      Agincourt North     0.000000   
3                                       Albion Gardens     0.000000   
4                                            Alderwood     0.000000   
5                                       Bathurst Manor     0.000000   
6                                        Bathurst Quay     0.000000   
7                                      Bayview Village     0.000000   
8                                     Beaumond Heights     0.000000   
9                                         Bedford Park     0.000000   
10                                         Berczy Park     0.000000   
11                                         Birch Cliff     0.000000   
12                                   Bloordale Gardens     0.000000   
13                                            Brockton     0.040000   
14   Business Reply Mail Processing Centre 969 Eastern     0.000000   
15                                         CFB Toronto     0.000000   
16                                            CN Tower     0.000000   
17                                         Cabbagetown     0.000000   
18                                 Caledonia-Fairbanks     0.000000   
19               Canada Post Gateway Processing Centre     0.000000   
20                                           Cedarbrae     0.000000   
21                                  Central Bay Street     0.014286   
22                                           Chinatown     0.000000   
23                                            Christie     0.000000   
24                                Church and Wellesley     0.024096   
25                                            Clairlea     0.000000   
26                                      Clarks Corners     0.000000   
27                                          Cliffcrest     0.000000   
28                                           Cliffside     0.000000   
29                                      Cliffside West     0.000000   
30                                          Cloverdale     0.000000   
31                                      Commerce Court     0.000000   
32                                          Davisville     0.000000   
33                                    Davisville North     0.000000   
34                                           Deer Park     0.000000   
35                                             Del Ray     0.000000   
36                                     Design Exchange     0.000000   
37                                     Don Mills North     0.000000   
38                                     Don Mills South     0.000000   
39                                         Dorset Park     0.000000   
40                                  Dovercourt Village     0.000000   
41                                           Downsview     0.000000   
42                                   Downsview Central     0.000000   
43                                      Downsview East     0.000000   
44                                     Downsview North     0.000000   
45                                 Downsview Northwest     0.000000   
46                                      Downsview West     0.000000   
47                                            Dufferin     0.000000   
48                                East Birchmount Park     0.000000   
49                                        East Toronto     0.000000   
50                                               Emery     0.000000   
51                                            Eringate     0.000000   
52                                    Exhibition Place     0.040000   
53                                            Fairview     0.000000   
54                                First Canadian Place     0.000000   
55                                     Flemingdon Park     0.00000

In [ ]:
toronto_grouped.shape

(206, 275)

In [ ]:
num_top_venues = 5

for hood in toronto_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Adelaide----
         venue  freq
0  Coffee Shop  0.06
1        Hotel  0.06
2         Café  0.05
3          Gym  0.04
4   Restaurant  0.04


----Agincourt----
                       venue  freq
0  Latin American Restaurant  0.25
1             Breakfast Spot  0.25
2                     Lounge  0.25
3             Clothing Store  0.25
4                Yoga Studio  0.00


----Agincourt North----
                        venue  freq
0                  Playground  0.25
1                Intersection  0.25
2                      Bakery  0.25
3                        Park  0.25
4  Modern European Restaurant  0.00


----Albion Gardens----
                  venue  freq
0         Grocery Store   0.2
1  Fast Food Restaurant   0.1
2   Fried Chicken Joint   0.1
3            Beer Store   0.1
4      Greek Restaurant   0.1


----Alderwood----
            venue  freq
0     Pizza Place  0.33
1             Gym  0.17
2     Coffee Shop  0.17
3             Pub  0.17
4  Sandwich Place  0.17


----Bathurst M

##Putting that into a pandas dataframe
First, let's write a function to sort the venues in descending order.

In [ ]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [ ]:
#Now let's create the new dataframe and display the top 10 venues for each neighborhood.

num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood      1st Most Common Venue 2nd Most Common Venue  \
0         Adelaide                Coffee Shop                 Hotel   
1        Agincourt  Latin American Restaurant        Breakfast Spot   
2  Agincourt North                 Playground          Intersection   
3   Albion Gardens              Grocery Store  Fast Food Restaurant   
4        Alderwood                Pizza Place                   Gym   

  3rd Most Common Venue 4th Most Common Venue       5th Most Common Venue  \
0                  Café                   Gym                  Restaurant   
1                Lounge        Clothing Store                 Yoga Studio   
2                Bakery                  Park  Modern European Restaurant   
3   Fried Chicken Joint            Beer Store            Greek Restaurant   
4           Coffee Shop                   Pub              Sandwich Place   

  6th Most Common Venue 7th Most Common Venue      8th Most Common Venue  \
0        Clothing Store       Thai Restaurant             Breakfast Spot   
1         Movie Theater                 Motel        Moroccan Restaurant   
2                 Motel   Moroccan Restaurant        Monument / Landmark   
3          Liquor Store           Pizza Place                   Pharmacy   
4         Metro Station    Mexican Restaurant  Middle Eastern Restaurant   

             9th Most Common Venue           10th Most Common Venue  
0                        Bookstore                       Steakhouse  
1              Monument / Landmark  Molecular Gastronomy Restaurant  
2  Molecular Gastronomy Restaurant                Mobile Phone Shop  
3                   Sandwich Place                      Men's Store  
4                      Men's Store               Miscellaneous Shop

In [ ]:
#neighborhoods_venues_sorted.to_csv('/content/drive/MyDrive/neighborhoods_venues_sorted.csv')

##Toronto rentals

In [ ]:
Toronto_apartment_rentals = pd.read_csv('/content/drive/MyDrive/Toronto_apartment_rentals.csv', sep=',', encoding='utf-8')
Toronto_apartment_rentals.head()

Bedroom  Bathroom  Den   Latitude  Longitude      Price
0        2       2.0    0  43.581639 -79.648193  $2,450.00
1        1       1.0    1  43.643051 -79.391643  $2,150.00
2        1       1.0    0  43.660605 -79.378635  $1,950.00
3        2       2.0    0  43.641087 -79.381405  $2,900.00
4        1       1.0    0  43.652487 -79.389622  $1,800.00

In [ ]:
#Toronto_apartment_rentals = Toronto_apartment_rentals.drop(columns=['Address'])
#Toronto_apartment_rentals = Toronto_apartment_rentals.rename(columns={'Lat':'Latitude', 'Long':'Longitude'})
#Toronto_apartment_rentals = Toronto_apartment_rentals.to_csv('/content/drive/MyDrive/Toronto_apartment_rentals.csv', index=False)
Toronto_apartment_rentals = pd.read_csv('/content/drive/MyDrive/Toronto_apartment_rentals.csv')
Toronto_apartment_rentals.head()


Bedroom  Bathroom  Den   Latitude  Longitude      Price
0        2       2.0    0  43.581639 -79.648193  $2,450.00
1        1       1.0    1  43.643051 -79.391643  $2,150.00
2        1       1.0    0  43.660605 -79.378635  $1,950.00
3        2       2.0    0  43.641087 -79.381405  $2,900.00
4        1       1.0    0  43.652487 -79.389622  $1,800.00

In [ ]:
# create map of Toronto using latitude and longitude values
map_toronto_rent = folium.Map(location=[latitude, longitude], zoom_start=12)

# add new markers to map of just the four boroughs containing Toronto
for lat, lng, Bedroom, Price in zip(Toronto_apartment_rentals['Latitude'], Toronto_apartment_rentals['Longitude'], Toronto_apartment_rentals['Bedroom'], Toronto_apartment_rentals['Price']):
    label = '{}, {}'.format(Bedroom, Price)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=8,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.5).add_to(map_toronto_rent)  
    
map_toronto_rent

##Totonto_downtown dataset

In [ ]:
# put the four boroughs into a new DataFrame
toronto_downtown = toronto_clean[toronto_clean['Borough'].isin(toronto_boroughs)].reset_index(drop=True)
print(toronto_downtown.shape)
toronto_downtown.head()

In [ ]:
toronto_downtown = pd.read_csv('/content/drive/MyDrive/toronto_downtown.csv')
toronto_downtown

In [ ]:
# create map of Toronto using latitude and longitude values
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=12)

# add new markers to map of just the four boroughs containing Toronto
for lat, lng, borough, neighborhood in zip(toronto_downtown['Latitude'], toronto_downtown['Longitude'], toronto_downtown['Borough'], toronto_downtown['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=8,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.5).add_to(map_toronto)  
    
map_toronto

##Clustering